Process for getting Polar zip file data into dataframe

In [100]:
#https://account.polar.com/ <-Go here to get polar data
import json
#import gzip  #<-not necessary
import datetime
from datetime import timedelta
import os, zipfile
import pandas as pd

In [4]:
data_zip=r"D:\OneDrive\Documents\learning\20210216ouraRingData\polarData\test_download20210801\polar-user-data-export_6103854c-9559-4056-8b5d-89feb507be70.zip"

In [16]:
polar_zip=zipfile.ZipFile(data_zip)

In [42]:
#read all files in zip to dictionary of file names and json (each value is a training_session)
polar_data_dict={}
for i in polar_zip.filelist:
    polar_data_dict[i.filename]=json.loads(polar_zip.read(i.filename))

In [ ]:
#make dictionary of dataframes for upload

In [159]:
polar_df_dict={}
for i,j in polar_data_dict.items():
    if 'training-session-' in i:
        #get utc delta training_session['timeZoneOffset']
        var_datetime_utc=j['timeZoneOffset']
        #get var_datetime_utc LIST
        var_datetime_utc_list=[datetime.datetime.strptime(
            k['dateTime']  ,'%Y-%m-%dT%H:%M:%S.%f') + timedelta(
                minutes=var_datetime_utc) for k in j['exercises'][0]['samples']['heartRate']]
        #get var_values LIST
        var_values_list=[k['value'] for k in j['exercises'][0]['samples']['heartRate']]
        
        df=pd.DataFrame(list(zip(var_datetime_utc_list,var_values_list)), columns=[
            'var_datetime_utc','var_value'
        ])
        #get var_activity training_session['name']
        df['var_activity']=j['name']
        #get var_periodicity
        df['var_periodicity']='seconds'
        #get vartype = heartrate
        df['var_type']='heart rate'
        #get var_unit 'heart rate per second'
        df['var_unit']='heart rate per second'
        #training_session_df['user_id']=1
        df['user_id']=1
        #get source_filename = i
        df['source_filename']=i
        df['time_stamp_utc']=datetime.datetime.utcnow()
        df['var_timezone_utc_delta_in_mins']=var_datetime_utc
        polar_df_dict[i]=df

Upload to the database

In [150]:
from LifeBuddyWebApp import create_app, db
from LifeBuddyWebApp.models import User, Post, Variables
proxyApp=create_app()
ctx=proxyApp.app_context()
ctx.push()
import time

C:\tools\miniconda3\envs\lifebuddy\lib\site-packages\flask_sqlalchemy\__init__.py:872: FSADeprecationWarning: SQLALCHEMY_TRACK_MODIFICATIONS adds significant overhead and will be disabled by default in the future.  Set it to True or False to suppress this warning.
  warnings.warn(FSADeprecationWarning(


In [160]:
#put investigations data into investigations table
start_time = time.time()
# df_inv.to_sql('investigations',db.engine, if_exists='append',index=False)
# df_re.to_sql('recalls',db.engine, if_exists='append',index=False)
skip_count=0
for i,j in polar_df_dict.items():
    if i not in [i[0] for i in db.session.query(Variables.source_filename).all()]:
        j.to_sql('variables',db.engine,if_exists='append', index=False)
    else:
        skip_count+=1
minutes=round((time.time()-start_time)/60)
seconds = (time.time()-start_time)%60
print(f'{minutes} mins and {seconds} seconds')

3 mins and 51.418614864349365 seconds


In [161]:
skip_count

0

In [163]:
#delete all rows in a table
Variables.query.delete()
db.session.commit()

228540

In [149]:
len(list(polar_df_dict.keys()))

224

In [162]:
polar_df_dict[list(polar_df_dict.keys())[75]]

var_datetime_utc  var_value var_activity var_periodicity  \
0   2021-03-25 06:28:32.122         68      Jogging         seconds   
1   2021-03-25 06:28:33.122         68      Jogging         seconds   
2   2021-03-25 06:28:34.122         68      Jogging         seconds   
3   2021-03-25 06:28:35.122         68      Jogging         seconds   
4   2021-03-25 06:28:36.122         69      Jogging         seconds   
..                      ...        ...          ...             ...   
599 2021-03-25 06:38:31.122        145      Jogging         seconds   
600 2021-03-25 06:38:32.122        145      Jogging         seconds   
601 2021-03-25 06:38:33.122        145      Jogging         seconds   
602 2021-03-25 06:38:34.122        145      Jogging         seconds   
603 2021-03-25 06:38:35.122        145      Jogging         seconds   

       var_type               var_unit  user_id  \
0    heart rate  heart rate per second        1   
1    heart rate  heart rate per second        1   
2    heart rate  heart rate per second        1   
3    heart rate  heart rate per second        1   
4    heart rate  heart rate per second        1   
..          ...                    ...      ...   
599  heart rate  heart rate per second        1   
600  heart rate  heart rate per second        1   
601  heart rate  heart rate per second        1   
602  heart rate  heart rate per second        1   
603  heart rate  heart rate per second        1   

                                       source_filename  \
0    training-session-2021-03-25-5831620089-5286a66...   
1    training-session-2021-03-25-5831620089-5286a66...   
2    training-session-2021-03-25-5831620089-5286a66...   
3    training-session-2021-03-25-5831620089-5286a66...   
4    training-session-2021-03-25-5831620089-5286a66...   
..                                                 ...   
599  training-session-2021-03-25-5831620089-5286a66...   
600  training-session-2021-03-25-5831620089-5286a66...   
601  training-session-2021-03-25-5831620089-5286a66...   
602  training-session-2021-03-25-5831620089-5286a66...   
603  training-session-2021-03-25-5831620089-5286a66...   

                time_stamp_utc  
0   2021-08-01 10:37:29.918788  
1   2021-08-01 10:37:29.918788  
2   2021-08-01 10:37:29.918788  
3   2021-08-01 10:37:29.918788  
4   2021-08-01 10:37:29.918788  
..                         ...  
599 2021-08-01 10:37:29.918788  
600 2021-08-01 10:37:29.918788  
601 2021-08-01 10:37:29.918788  
602 2021-08-01 10:37:29.918788  
603 2021-08-01 10:37:29.918788  

[604 rows x 9 columns]

In [131]:
polar_df_dict

{'training-session-2021-03-25-5833693154-003b4bf2-e18f-46ad-87df-9254d8434062.json': [datetime.datetime(2021, 3, 25, 18, 49, 12, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 13, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 14, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 15, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 16, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 17, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 18, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 19, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 20, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 21, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 22, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 23, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 24, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 25, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 26, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 27, 443000),
  datetime.datetime(2021, 3, 25, 18, 49, 28, 443000)

In [126]:
test_list=[]
for i,j in polar_data_dict.items():
    
    test_list.append(i)

In [129]:
test_list[0]

'training-session-2021-03-25-5833693154-003b4bf2-e18f-46ad-87df-9254d8434062.json'

In [ ]:
training_session_df['var_activity']=training_session['name']
training_session_df['var_type']='heart rate'
# training_session_df['var_datetime_utc']
training_session_df['var_periodicity']='seconds'
# training_session_df['var_value']
training_session_df['var_unit']='heart rate per second'
training_session_df['var_timezone_utc_delta_in_mins']=training_session['timeZoneOffset']
training_session_df['user_id']=1

In [118]:
list(polar_data_dict.keys())[0]

'training-session-2021-03-25-5833693154-003b4bf2-e18f-46ad-87df-9254d8434062.json'

In [117]:
polar_data_dict['training-session-2021-06-20-6179915259-fed3075c-4406-43ec-8992-05ada8127914.json']

{'exportVersion': '1.3',
 'name': 'Walking',
 'feeling': '0.4000000059604645',
 'latitude': 38.83371934414463,
 'longitude': -77.04806063125095,
 'startTime': '2021-06-20T09:11:48.177',
 'stopTime': '2021-06-20T09:22:04.177',
 'timeZoneOffset': -240,
 'distance': 908.0629272460938,
 'duration': 'PT616S',
 'maximumHeartRate': 167,
 'averageHeartRate': 112,
 'kiloCalories': 80,
 'physicalInformationSnapshot': {'dateTime': '2021-06-20T13:22:10.000',
  'sex': 'MALE',
  'birthday': '1981-02-19',
  'height, cm': 178.0,
  'weight, kg': 75.0,
  'vo2Max': 50,
  'maximumHeartRate': 180,
  'functionalThresholdPower': 299},
 'exercises': [{'startTime': '2021-06-20T09:11:48.177',
   'stopTime': '2021-06-20T09:22:04.177',
   'timezoneOffset': -240,
   'duration': 'PT616S',
   'distance': 908.0629272460938,
   'sport': 'WALKING',
   'latitude': 38.83371934414463,
   'longitude': -77.04806063125095,
   'kiloCalories': 80,
   'heartRate': {'min': 100, 'avg': 112, 'max': 167},
   'speed': {'avg': 5.3068

In [87]:
#A single exercise session
training_session=polar_data_dict[list(polar_data_dict.keys())[0]]

In [82]:
# exercies (hr, speed, dist) data from one training session
training_session_dets=polar_data_dict[list(polar_data_dict.keys())[0]]['exercises'][0]['samples']
training_session_dets['heartRate']

[{'dateTime': '2021-03-25T18:49:12.443', 'value': 105},
 {'dateTime': '2021-03-25T18:49:13.443', 'value': 103},
 {'dateTime': '2021-03-25T18:49:14.443', 'value': 103},
 {'dateTime': '2021-03-25T18:49:15.443', 'value': 102},
 {'dateTime': '2021-03-25T18:49:16.443', 'value': 102},
 {'dateTime': '2021-03-25T18:49:17.443', 'value': 102},
 {'dateTime': '2021-03-25T18:49:18.443', 'value': 101},
 {'dateTime': '2021-03-25T18:49:19.443', 'value': 101},
 {'dateTime': '2021-03-25T18:49:20.443', 'value': 100},
 {'dateTime': '2021-03-25T18:49:21.443', 'value': 100},
 {'dateTime': '2021-03-25T18:49:22.443', 'value': 99},
 {'dateTime': '2021-03-25T18:49:23.443', 'value': 98},
 {'dateTime': '2021-03-25T18:49:24.443', 'value': 98},
 {'dateTime': '2021-03-25T18:49:25.443', 'value': 97},
 {'dateTime': '2021-03-25T18:49:26.443', 'value': 97},
 {'dateTime': '2021-03-25T18:49:27.443', 'value': 97},
 {'dateTime': '2021-03-25T18:49:28.443', 'value': 97},
 {'dateTime': '2021-03-25T18:49:29.443', 'value': 97},


In [60]:
#make dataframes

In [83]:
#name of activity
polar_data_dict[list(polar_data_dict.keys())[0]]['name']
#time difference from utc ex. recorded time - timeZoneOffset = corresponding utc time
polar_data_dict[list(polar_data_dict.keys())[0]]['timeZoneOffset']

-240

In [84]:
#This is the time format
datetime.datetime.strptime(training_session_dets['heartRate'][0]['dateTime']  ,'%Y-%m-%dT%H:%M:%S.%f')

datetime.datetime(2021, 3, 25, 18, 49, 12, 443000)

In [85]:
#heart rate
training_session_dets['heartRate'][0]['value'] 

105

In [99]:
datetime_list=[]
heartrate_list=[]
for i in training_session['exercises'][0]['samples']['heartRate']:
    datetime_list.append(datetime.datetime.strptime(
        i['dateTime']  ,'%Y-%m-%dT%H:%M:%S.%f')+ timedelta(minutes=training_session['timeZoneOffset']))
    heartrate_list.append(i['value'])
    

In [94]:
training_session['timeZoneOffset']

-240

In [90]:
len(heartrate_list)

245

In [93]:
datetime_list[0]

datetime.datetime(2021, 3, 25, 18, 49, 12, 443000)

In [98]:
datetime_list[0] + timedelta(minutes=training_session['timeZoneOffset'])

datetime.datetime(2021, 3, 25, 14, 49, 12, 443000)

In [105]:
training_session_df=pd.DataFrame(list(zip(datetime_list, heartrate_list)),columns=['var_datetime_utc','var_value'])

In [106]:
training_session_df.head()

var_datetime_utc  var_value
0 2021-03-25 14:49:12.443        105
1 2021-03-25 14:49:13.443        103
2 2021-03-25 14:49:14.443        103
3 2021-03-25 14:49:15.443        102
4 2021-03-25 14:49:16.443        102

In [107]:
training_session_df['var_activity']=training_session['name']
training_session_df['var_type']='heart rate'
# training_session_df['var_datetime_utc']
training_session_df['var_periodicity']='seconds'
# training_session_df['var_value']
training_session_df['var_unit']='heart rate per second'
training_session_df['var_timezone_utc_delta_in_mins']=training_session['timeZoneOffset']
training_session_df['var_unit']=1

In [108]:
training_session_df.head()

var_datetime_utc  var_value activity var_periodicity
0 2021-03-25 14:49:12.443        105  Walking         seconds
1 2021-03-25 14:49:13.443        103  Walking         seconds
2 2021-03-25 14:49:14.443        103  Walking         seconds
3 2021-03-25 14:49:15.443        102  Walking         seconds
4 2021-03-25 14:49:16.443        102  Walking         seconds

In [20]:
list(polar_data_dict.keys())[1]

<ZipInfo filename='training-session-2021-06-07-6130436929-01765f57-8962-4cb9-8112-2067cd7aada8.json' compress_type=deflate file_size=127265 compress_size=9896>

In [31]:
polar_zip.filelist[0].filename

'training-session-2021-03-25-5833693154-003b4bf2-e18f-46ad-87df-9254d8434062.json'

In [32]:
polar_zip.filelist[0].date_time

(2021, 8, 1, 6, 12, 48)

In [30]:
dir(polar_zip.filelist[0])

['CRC',
 'FileHeader',
 '__class__',
 '__delattr__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__slots__',
 '__str__',
 '__subclasshook__',
 '_compresslevel',
 '_decodeExtra',
 '_encodeFilenameFlags',
 '_raw_time',
 'comment',
 'compress_size',
 'compress_type',
 'create_system',
 'create_version',
 'date_time',
 'external_attr',
 'extra',
 'extract_version',
 'file_size',
 'filename',
 'flag_bits',
 'from_file',
 'header_offset',
 'internal_attr',
 'is_dir',
 'orig_filename',
 'reserved',
 'volume']

In [14]:
a_json=json.loads(zipfile.ZipFile(data_zip).read(
    'training-session-2021-05-09-6018580194-30bd2f19-32e2-4109-9552-6091a3c57589.json'))

In [15]:
a_json

{'exportVersion': '1.3',
 'name': 'Yoga',
 'feeling': '0.4000000059604645',
 'startTime': '2021-05-09T13:08:37.645',
 'stopTime': '2021-05-09T13:21:04.645',
 'timeZoneOffset': -240,
 'duration': 'PT747S',
 'maximumHeartRate': 146,
 'averageHeartRate': 123,
 'kiloCalories': 119,
 'physicalInformationSnapshot': {'dateTime': '2021-05-09T17:21:10.000',
  'sex': 'MALE',
  'birthday': '1981-02-19',
  'height, cm': 178.0,
  'weight, kg': 75.0,
  'vo2Max': 50,
  'maximumHeartRate': 180,
  'functionalThresholdPower': 299},
 'exercises': [{'startTime': '2021-05-09T13:08:37.645',
   'stopTime': '2021-05-09T13:21:04.645',
   'timezoneOffset': -240,
   'duration': 'PT747S',
   'sport': 'YOGA',
   'kiloCalories': 119,
   'heartRate': {'min': 108, 'avg': 123, 'max': 146},
   'zones': {'fit_fat': [{'lowerLimit': 0,
      'higherLimit': 122,
      'inZone': 'PT422S',
      'zoneIndex': 1},
     {'lowerLimit': 122,
      'higherLimit': 240,
      'inZone': 'PT326S',
      'zoneIndex': 2}],
    'heart_ra

In [11]:
dir(zipfile.ZipFile(data_zip).extract)

['__call__',
 '__class__',
 '__delattr__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__func__',
 '__ge__',
 '__get__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__self__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__']